Group members: Aparna Aidith, Abraham George, Mike Shin, Junyan Shao, Shuai Ye

Target Restaurant: Mexican

Report

Task A: After reading the scraped data of the restaurants, we cleaned the data by dropping the columns that are useless to us (retaining the three requested columns). 

Task B: We replaced the keywords in the comments to one of the four attributes they belonged to, so we can conduct sentiment analysis. For instance, we replaced “taste”, “smell”, and “vegan” to the attribute name “food”. 

Task C: We calculated the word frequency of words in the comments after replacing them to different attributes. 

Task D (part one): In order to recommend similar restaurants to customers, we grouped the restaurants by their name and calculated the average rating of them. Then, we performed the cosine similarity analysis to the restaurants.

Task D (part two): To better recommend the restaurants to the customers, we conducted a sentiment analysis of the restaurants and sorted them by their score (high to low). 

Task E: We built and tested a recommendation function, so the system will recommend the top three restaurants to the customer given the index of a restaurant the customer has already been to (based on cosine similarity and sentiment analysis).

Task F: We built another recommendation system which is simply based on the rating of the restaurants. Comparing to the recommendations generated from Task E, these restaurants have much lower cosine similarity score and sentiment analysis score. In conclusion, the recommendations generated simply from the ratings are not meeting the requirement of the customers.


In [75]:
import pandas as pd

data = pd.read_csv("restaurants_page2.csv")
data.shape

(8022, 8)

In [4]:
data.head()

web-scraper-order                              web-scraper-start-url  \
0  1541101129-15403  https://www.yelp.com/search?find_desc=Restaura...   
1  1541100592-11699  https://www.yelp.com/search?find_desc=Restaura...   
2  1541100469-10772  https://www.yelp.com/search?find_desc=Restaura...   
3  1541100934-14030  https://www.yelp.com/search?find_desc=Restaura...   
4  1541100934-14027  https://www.yelp.com/search?find_desc=Restaura...   

      restaurant_links                              restaurant_links-href  \
0  Austin Taco Project  https://www.yelp.com/biz/austin-taco-project-a...   
1     Matt’s El Rancho  https://www.yelp.com/biz/matts-el-rancho-austi...   
2        Casa Garcia’s  https://www.yelp.com/biz/casa-garcias-austin-3...   
3          Zocalo Café  https://www.yelp.com/biz/zocalo-caf%C3%A9-aust...   
4          Zocalo Café  https://www.yelp.com/biz/zocalo-caf%C3%A9-aust...   

                                         review_text  \
0  I went here with my boyfriend one evening. It ...   
1                                                NaN   
2                                                NaN   
3  I don't typically care for restaurants that do...   
4  I really love this place and it's one of my fa...   

                                             ratings  review_pages  \
0                                                NaN           7.0   
1  <img class="offscreen" height="303" src="https...           5.0   
2  <img class="offscreen" height="303" src="https...           NaN   
3                                                NaN           9.0   
4                                                NaN           9.0   

                                   review_pages-href  
0  https://www.yelp.com/biz/austin-taco-project-a...  
1  https://www.yelp.com/biz/matts-el-rancho-austi...  
2                                                NaN  
3  https://www.yelp.com/biz/zocalo-caf%C3%A9-aust...  
4  https://www.yelp.com/biz/zocalo-caf%C3%A9-aust...

In [5]:
import math
import re
def replace(s):
    #if (math.isnan((s))
    if isinstance(s, str):
        if 'alt' in s:
            return re.search(r'alt="(.+) star rating"', s).group(1)

In [6]:
def replace_to_float(s):
    #if (math.isnan((s))
    return float(s)

In [7]:
# Drop Columns
data_cleaned = data.drop(columns=['web-scraper-order','web-scraper-start-url', 'restaurant_links-href', 'review_pages', 'review_pages-href' ])
data_cleaned['ratings'] = data_cleaned['ratings'].apply(replace)
#fill nan
data_cleaned['review_text'] = data_cleaned['review_text'].fillna('None')
data_cleaned['ratings'] = data_cleaned['ratings'].fillna(0)
data_cleaned['ratings'] = data_cleaned['ratings'].apply(replace_to_float)
data_cleaned['ratings'] = data_cleaned['ratings'].replace(0.0, data_cleaned['ratings'].mean())

In [8]:
data_cleaned.head()

restaurant_links                                        review_text  \
0  Austin Taco Project  I went here with my boyfriend one evening. It ...   
1     Matt’s El Rancho                                               None   
2        Casa Garcia’s                                               None   
3          Zocalo Café  I don't typically care for restaurants that do...   
4          Zocalo Café  I really love this place and it's one of my fa...   

    ratings  
0  1.953004  
1  1.000000  
2  3.000000  
3  1.953004  
4  1.953004

In [9]:
food_words = ['quality','taste','calories','size','amount','smell','look','health','healthy','vegan','spicy','sweet','sour','hot','cold','cool','ethnic','bitter','drinks','drink','salt','salty']
service = ["speed","friendliness","couteous","polite","rude","pleasant","quick","slow","friendly"]
price = ["costly","expensive","cheap","pricy","affordable","average"]
location = ["parking", "easy to find", "drive-through", "drive through",
           "accessible", "accessibility","paid parking", "traffic", "scenery", "view", "free parking"]

In [10]:
searchfor_food_word = ['quality','taste','calories','size','amount','smell','look','health','healthy','vegan','spicy','sweet','sour','hot','cold','cool','ethnic','bitter','drinks','drink','salt','salty']

In [11]:
searchfor_service = ["speed","friendliness","couteous","polite","rude","pleasant","quick","slow","friendly"]

In [12]:
searchfor_price = ["costly","expensive","cheap","pricy","affordable","average"]

In [13]:
searchfor_location = ["parking", "easy to find", "drive-through", "drive through","accessible", "accessibility","paid parking", "traffic", "scenery", "view", "free parking"]

In [14]:
sentiment_text = data_cleaned['review_text']
#iterate through the entire text sentiment_text[0]
sentiment_text = sentiment_text.to_frame()


# run the if statement above for all text
#for index in range(len(sentiment_text)):
food_word_reviews = sentiment_text[sentiment_text.review_text.str.contains('|'.join(searchfor_food_word))]
service_reviews = sentiment_text[sentiment_text.review_text.str.contains('|'.join(searchfor_service))]
price_reviews = sentiment_text[sentiment_text.review_text.str.contains('|'.join(searchfor_price))]
location_reviews = sentiment_text[sentiment_text.review_text.str.contains('|'.join(searchfor_location))]

In [15]:
import re
all_documents = []


review_data = data_cleaned['review_text']
review_data = pd.DataFrame(review_data)


In [16]:
import numpy as np

review_text = np.asarray(review_data)

In [17]:
words = []
for i in review_text:
    words.append(i)

In [18]:
i = 0
while i < 5:
    print(words[i])
    i+=1

['I went here with my boyfriend one evening. It was a place that I think he found on Yelp. We just wanted to go to somewhere different. \nIt was good. Taste of Tacos is paramount. I approve. I would go back.']
['None']
['None']
['I don\'t typically care for restaurants that do not offer table service and Zocalo Café is no exception to this rule. \xa0I always think the restaurant, while saving the hassle of employing waiters, they potentially lose out on the subsequent orders you may want to make, for another drink, or dessert, or what have you. \xa0\n\nOne interesting thing that I noticed at Zocalo was, despite the lack of waiters, they sure did have a lot of people itching to clear our plates that were still half full of food and take our water glasses that we were still drinking from them. \xa0Even one of my dining companions chided me for saying "No" to one of the plate-vultures in a loud tone and not saying "No, thank you". \xa0In my defense, their resident DJ was really blasting t

In [19]:
review_string  = ''.join(str(words))
review_string

'[array([\'I went here with my boyfriend one evening. It was a place that I think he found on Yelp. We just wanted to go to somewhere different. \\nIt was good. Taste of Tacos is paramount. I approve. I would go back.\'],\n      dtype=object), array([\'None\'], dtype=object), array([\'None\'], dtype=object), array([\'I don\\\'t typically care for restaurants that do not offer table service and Zocalo Café is no exception to this rule. \\xa0I always think the restaurant, while saving the hassle of employing waiters, they potentially lose out on the subsequent orders you may want to make, for another drink, or dessert, or what have you. \\xa0\\n\\nOne interesting thing that I noticed at Zocalo was, despite the lack of waiters, they sure did have a lot of people itching to clear our plates that were still half full of food and take our water glasses that we were still drinking from them. \\xa0Even one of my dining companions chided me for saying "No" to one of the plate-vultures in a loud

In [20]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /Users/junyan/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [21]:
from nltk.corpus import stopwords 
from nltk.tokenize import word_tokenize 
tokens = word_tokenize(review_string)

tokens

['[',
 'array',
 '(',
 '[',
 "'I",
 'went',
 'here',
 'with',
 'my',
 'boyfriend',
 'one',
 'evening',
 '.',
 'It',
 'was',
 'a',
 'place',
 'that',
 'I',
 'think',
 'he',
 'found',
 'on',
 'Yelp',
 '.',
 'We',
 'just',
 'wanted',
 'to',
 'go',
 'to',
 'somewhere',
 'different',
 '.',
 '\\nIt',
 'was',
 'good',
 '.',
 'Taste',
 'of',
 'Tacos',
 'is',
 'paramount',
 '.',
 'I',
 'approve',
 '.',
 'I',
 'would',
 'go',
 'back',
 '.',
 "'",
 ']',
 ',',
 'dtype=object',
 ')',
 ',',
 'array',
 '(',
 '[',
 "'None",
 "'",
 ']',
 ',',
 'dtype=object',
 ')',
 ',',
 'array',
 '(',
 '[',
 "'None",
 "'",
 ']',
 ',',
 'dtype=object',
 ')',
 ',',
 'array',
 '(',
 '[',
 "'I",
 "don\\'t",
 'typically',
 'care',
 'for',
 'restaurants',
 'that',
 'do',
 'not',
 'offer',
 'table',
 'service',
 'and',
 'Zocalo',
 'Café',
 'is',
 'no',
 'exception',
 'to',
 'this',
 'rule',
 '.',
 '\\xa0I',
 'always',
 'think',
 'the',
 'restaurant',
 ',',
 'while',
 'saving',
 'the',
 'hassle',
 'of',
 'employing',
 'waite

In [22]:
import enchant
punctuations = ['(',')',';',':','[',']',',', '.', '&', '\n', '=', '∈','@',"#",'»','!','\'','``',"''",'...','?']
stop_words = stopwords.words('english')
englishDictionary = enchant.Dict("en_US")
keywords = [word for word in tokens if not word in stop_words and not word in punctuations]

In [23]:
import re

review_clean_text = re.sub('[^a-zA-Z-]+', ' ', str(keywords))
#text_clean_step_0_result

In [24]:
clean_words = []
for i in review_clean_text:
    clean_words.append(i)

In [25]:
final_review_text = ''.join(clean_words)
final_review_text = final_review_text.lower()
final_review_text

' array i went boyfriend one evening it place i think found yelp we wanted go somewhere different nit good taste tacos paramount i approve i would go back dtype object array none dtype object array none dtype object array i don t typically care restaurants offer table service zocalo caf exception rule xa i always think restaurant saving hassle employing waiters potentially lose subsequent orders may want make another drink dessert xa n none interesting thing i noticed zocalo despite lack waiters sure lot people itching clear plates still half full food take water glasses still drinking xa even one dining companions chided saying no one plate-vultures loud tone saying no thank xa in defense resident dj really blasting dub-step i wanted make sure plate-vulture heard absconding last half crispy enchiladas xa not mention i find rather rude someone clearing people s plates would put dirty thumb plate without asking first xa ew xa n ndespite weirdness walk ordering crazy chips salsa line pla

In [26]:
def count_word(str):
    counts = dict()
    words = str.split()

    for word in words:
        if word in counts:
            counts[word] += 1
        else:
            counts[word] = 1

    return counts

review_word_freq = count_word(final_review_text)

In [27]:
import operator

final_frequencyOfWords = sorted(review_word_freq.items(), key=operator.itemgetter(1),reverse = True)

In [28]:
def Convert(lists, di): 
    for a, b in lists: 
        di.setdefault(a, []).append(b) 
    return di

In [29]:
frequency_dict = {}
word_frequency = Convert(final_frequencyOfWords,frequency_dict)

In [30]:
import csv

with open('review_frequency1.csv', 'w') as f:
    fieldnames = ['word', 'frequency']
    writer = csv.DictWriter(f, fieldnames=fieldnames)
    writer.writeheader()
    data = [dict(zip(fieldnames, [k, v])) for k, v in word_frequency.items()]
    writer.writerows(data)

In [31]:
import pandas as pd
results = pd.read_csv('review_frequency1.csv', encoding = "ISO-8859-1")
results

word frequency
0                    i   [10610]
1                array    [8027]
2                dtype    [8022]
3               object    [8022]
4                    n    [6308]
5                   xa    [5651]
6                 none    [4074]
7                  the    [3674]
8                 food    [3009]
9                    t    [2697]
10                good    [2598]
11               tacos    [2488]
12                   s    [2459]
13               place    [2382]
14               great    [1903]
15                taco    [1657]
16                like    [1334]
17                  it    [1329]
18             service    [1277]
19               salsa    [1215]
20                 one    [1146]
21                  we    [1121]
22                 get    [1119]
23             mexican    [1119]
24              really    [1118]
25              austin    [1080]
26                back    [1017]
27                  go     [989]
28                time     [931]
29               would     [916]
...                ...       ...
13047           ironed       [1]
13048           molded       [1]
13049            swine       [1]
13050        reheating       [1]
13051  semi-vegetarian       [1]
13052              esp       [1]
13053         highball       [1]
13054       reinvented       [1]
13055   well-developed       [1]
13056    sports-barish       [1]
13057     kid-friendly       [1]
13058          betwixt       [1]
13059     romanticizes       [1]
13060    reincarnation       [1]
13061     historically       [1]
13062         relevant       [1]
13063          forsure       [1]
13064        braunfels       [1]
13065         praising       [1]
13066        superhero       [1]
13067            asset       [1]
13068         gracious       [1]
13069         accounts       [1]
13070           gentle       [1]
13071         threaten       [1]
13072             cops       [1]
13073        bullstuff       [1]
13074         steering       [1]
13075    embarrassment       [1]
13076    automatically       [1]

[13077 rows x 2 columns]

In [32]:
attribute_count = dict()
attributes =  ['service','food','price','location']
for word in final_frequencyOfWords:
    for value in attributes:
        if word[0] == value:
            attribute_count.update({word[0] : word[1]})
        else:
            continue
            
attribute_count

{'food': 3009, 'service': 1277, 'price': 281, 'location': 219}

In [33]:
from __future__ import division
import string
import math

tokenize = lambda doc: doc.lower().split(" ")

In [34]:
data_cleaned.head()

restaurant_links                                        review_text  \
0  Austin Taco Project  I went here with my boyfriend one evening. It ...   
1     Matt’s El Rancho                                               None   
2        Casa Garcia’s                                               None   
3          Zocalo Café  I don't typically care for restaurants that do...   
4          Zocalo Café  I really love this place and it's one of my fa...   

    ratings  
0  1.953004  
1  1.000000  
2  3.000000  
3  1.953004  
4  1.953004

In [35]:
grouped_by_restaurant1 = data_cleaned.groupby(['restaurant_links'])[['review_text']].apply(lambda x: x.sum())
grouped_by_restaurant2 = data_cleaned.groupby(['restaurant_links'])[['ratings']].mean()

grouped_by_restaurant = grouped_by_restaurant1.merge(grouped_by_restaurant2, on='restaurant_links', how='inner')

In [36]:
grouped_by_restaurant

review_text  \
restaurant_links                                                                          
Austin Taco Project                   I went here with my boyfriend one evening. It ...   
Brendas All Natural                   Amazing breakfast tacos!! Lady was super frien...   
Camino Real Restaurant                I don't live close to this place, but when I'm...   
Casa Garcia’s                         NoneNoneWhen I'm in town I have to hit this pl...   
Casa Maria                            I love this place, their breakfast tacos are a...   
El Taquito                            Good for really late when most of the other tr...   
Juan In A Million                     NoneNoneGreat breakfast at great prices. Very ...   
La Condesa                            Great service but portions very small for the ...   
La Fruta Feliz                        NoneNoneNoneMy heart. Good food, sweet service...   
La Morena                             Went in for quick treat knowing they had ice c...   
Los Jaliscienses                      Food quality and atmosphere are not the issue ...   
Manuel’s                              Warning- ripoff scam in progress! I had my din...   
Matt’s El Rancho                      NoneI was pleasantly surprised by this place. ...   
Papalote Taco House                   We tried 4 different tacos and they were all o...   
Pueblo Viejo                          NoneOrdered the taco plate which came with bea...   
Santa Catarina Restaurant             NoneNoneTwo years this place has been here and...   
Taco Flats                            Love love love love love!! Amazing food amazin...   
Taco More                             NoneNoneNoneI went here with my Boyfriend and ...   
Tamale House East                     Finally I found a decent place that has good t...   
Taquería Chapala                      This place is awesome! If you are looking for ...   
Techo Mezcaleria & Agave Bar          NoneFriend: "'Techo' is Spanish for roof."\n\n...   
Tex-Mex Joe’s                         It was hard to have high expectations,as the r...   
Tortilleria Rio Grande                NoneI really wanted to like this place they ha...   
Uncle Julio’s                         The fajitas were the bomb.  Marquis made an aw...   
Vazquez Restaurant                    NoneNoneVery good Mexican food, good Serrvicce...   
Zocalo Café                           I don't typically care for restaurants that do...   
Z’Tejas Mexican Restaurant and Grill  NoneNoneGrateful for the complimentary valet a...   

                                       ratings  
restaurant_links                                
Austin Taco Project                   2.909835  
Brendas All Natural                   3.476502  
Camino Real Restaurant                2.877737  
Casa Garcia’s                         3.029280  
Casa Maria                            2.882058  
El Taquito                            2.862613  
Juan In A Million                     2.993169  
La Condesa                            2.532058  
La Fruta Feliz                        3.086258  
La Morena                             3.476502  
Los Jaliscienses                      2.940212  
Manuel’s                              2.807058  
Matt’s El Rancho                      2.793169  
Papalote Taco House                   3.176502  
Pueblo Viejo                          3.162613  
Santa Catarina Restaurant             3.112613  
Taco Flats                            2.965391  
Taco More                             3.148724  
Tamale House East                     2.837613  
Taquería Chapala                      2.928354  
Techo Mezcaleria & Agave Bar          3.251502  
Tex-Mex Joe’s                         3.054021  
Tortilleria Rio Grande                3.073724  
Uncle Julio’s                         2.654280  
Vazquez Restaurant                    2.956094  
Zocalo Café                           2.957058  
Z’Tejas Mexican Restaurant and Grill  2.668169

In [37]:
all_documents = []
for index, row in grouped_by_restaurant.iterrows():
       all_documents.append(row['review_text'])

In [38]:
from sklearn.feature_extraction.text import TfidfVectorizer

vectorizer = TfidfVectorizer()
X = vectorizer.fit_transform(all_documents)

In [39]:
import sklearn
cosine = sklearn.metrics.pairwise.cosine_similarity(X, Y=None, dense_output=True)

In [40]:
type(cosine)

numpy.ndarray

In [41]:
cosine = pd.DataFrame(cosine)

In [42]:
cosine

0         1         2         3         4         5         6   \
0   1.000000  0.524435  0.923809  0.920699  0.929775  0.950208  0.905198   
1   0.524435  1.000000  0.540910  0.543146  0.534377  0.540483  0.507040   
2   0.923809  0.540910  1.000000  0.959868  0.955522  0.951010  0.920526   
3   0.920699  0.543146  0.959868  1.000000  0.963175  0.947672  0.916207   
4   0.929775  0.534377  0.955522  0.963175  1.000000  0.947365  0.917193   
5   0.950208  0.540483  0.951010  0.947672  0.947365  1.000000  0.918601   
6   0.905198  0.507040  0.920526  0.916207  0.917193  0.918601  1.000000   
7   0.944499  0.517004  0.944610  0.934166  0.945010  0.941943  0.912561   
8   0.925969  0.549211  0.933867  0.930417  0.929829  0.949797  0.902561   
9   0.339322  0.171960  0.357538  0.364140  0.357267  0.353962  0.347609   
10  0.934670  0.547299  0.961256  0.953772  0.955901  0.952917  0.922695   
11  0.938989  0.505057  0.946801  0.943575  0.949055  0.936751  0.913143   
12  0.918080  0.503671  0.938517  0.933222  0.934855  0.930192  0.902854   
13  0.932156  0.551976  0.925846  0.920419  0.918346  0.953413  0.904618   
14  0.939855  0.540195  0.921974  0.915814  0.918096  0.954099  0.909148   
15  0.918067  0.536527  0.949446  0.947692  0.945091  0.934879  0.903425   
16  0.951074  0.526762  0.939692  0.935076  0.936911  0.955309  0.914157   
17  0.933802  0.541377  0.947913  0.941288  0.936775  0.961944  0.913690   
18  0.930087  0.526952  0.936832  0.930858  0.932069  0.940710  0.907541   
19  0.918376  0.538678  0.960510  0.950416  0.945950  0.952854  0.915504   
20  0.741932  0.442398  0.768032  0.757962  0.750164  0.756422  0.731582   
21  0.929067  0.564474  0.957244  0.958144  0.952246  0.951426  0.914152   
22  0.905050  0.550500  0.934868  0.934263  0.924697  0.940216  0.899365   
23  0.937968  0.506992  0.946684  0.944676  0.949047  0.938393  0.914333   
24  0.933485  0.562451  0.960159  0.956914  0.952363  0.961254  0.923297   
25  0.908967  0.519385  0.934240  0.928683  0.926174  0.928504  0.895335   
26  0.926425  0.491820  0.938413  0.931511  0.936747  0.930847  0.904723   

          7         8         9     ...           17        18        19  \
0   0.944499  0.925969  0.339322    ...     0.933802  0.930087  0.918376   
1   0.517004  0.549211  0.171960    ...     0.541377  0.526952  0.538678   
2   0.944610  0.933867  0.357538    ...     0.947913  0.936832  0.960510   
3   0.934166  0.930417  0.364140    ...     0.941288  0.930858  0.950416   
4   0.945010  0.929829  0.357267    ...     0.936775  0.932069  0.945950   
5   0.941943  0.949797  0.353962    ...     0.961944  0.940710  0.952854   
6   0.912561  0.902561  0.347609    ...     0.913690  0.907541  0.915504   
7   1.000000  0.922689  0.351913    ...     0.927740  0.934830  0.934821   
8   0.922689  1.000000  0.341237    ...     0.950812  0.922974  0.940897   
9   0.351913  0.341237  1.000000    ...     0.355540  0.351775  0.350353   
10  0.954571  0.944238  0.353149    ...     0.946587  0.942103  0.959416   
11  0.963844  0.914738  0.360765    ...     0.925791  0.933376  0.936802   
12  0.938499  0.900720  0.366950    ...     0.912676  0.916587  0.922570   
13  0.909374  0.940480  0.351289    ...     0.947921  0.921183  0.929421   
14  0.914844  0.934315  0.344908    ...     0.942893  0.923866  0.925734   
15  0.951395  0.917244  0.336268    ...     0.925050  0.925975  0.941017   
16  0.946384  0.934000  0.357500    ...     0.945482  0.935537  0.932585   
17  0.927740  0.950812  0.355540    ...     1.000000  0.929283  0.953336   
18  0.934830  0.922974  0.351775    ...     0.929283  1.000000  0.930508   
19  0.934821  0.940897  0.350353    ...     0.953336  0.930508  1.000000   
20  0.762587  0.749806  0.267355    ...     0.762891  0.748692  0.763101   
21  0.932994  0.939424  0.350736    ...     0.945825  0.936320  0.950137   
22  0.900383  0.937736  0.347884    ...     0.944964  0.912316  0.934410   
23  0.960554  0.914197  0.364716    ...     0.924036  0.9

### Sentiment Analysis

In [43]:
from nltk.sentiment.vader import SentimentIntensityAnalyzer
import nltk
nltk.download('vader_lexicon')
sid = SentimentIntensityAnalyzer()

[nltk_data] Downloading package vader_lexicon to
[nltk_data]     /Users/junyan/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


/anaconda3/lib/python3.6/site-packages/nltk/twitter/__init__.py:20: UserWarning: The twython library has not been installed. Some functionality from the twitter package will not be available.
  warnings.warn("The twython library has not been installed. "


In [44]:
review1= data_cleaned

In [45]:
review1 = review1.set_index(['restaurant_links'])

In [46]:
sentiment_analysis2 = pd.DataFrame()
sentiment_analysis2 = review1['review_text'].apply(sid.polarity_scores)

In [47]:
sentiment_analysis2=pd.DataFrame(sentiment_analysis2)

In [48]:
for index, row in sentiment_analysis2.iterrows():
    row['review_text'] = row['review_text']['compound']

In [49]:
sentiment_analysis2

review_text
restaurant_links                                
Austin Taco Project                       0.4404
Matt’s El Rancho                               0
Casa Garcia’s                                  0
Zocalo Café                               0.9802
Zocalo Café                               0.9985
Manuel’s                                  0.6681
Taquería Chapala                          0.9488
Tamale House East                         0.7574
Tortilleria Rio Grande                         0
Uncle Julio’s                             0.9705
Camino Real Restaurant                    0.9108
Pueblo Viejo                                   0
Tortilleria Rio Grande                    0.9715
Tortilleria Rio Grande                    0.9636
Camino Real Restaurant                   -0.6249
Juan In A Million                              0
Los Jaliscienses                         -0.4466
Santa Catarina Restaurant                      0
Taco Flats                                0.9898
Juan In A Million                              0
Tamale House East                        -0.0516
El Taquito                                0.3084
Los Jaliscienses                          0.9265
Taquería Chapala                          0.9634
Z’Tejas Mexican Restaurant and Grill           0
Manuel’s                                       0
Taco More                                      0
Vazquez Restaurant                             0
Tamale House East                         0.7778
Z’Tejas Mexican Restaurant and Grill           0
...                                          ...
Z’Tejas Mexican Restaurant and Grill           0
Santa Catarina Restaurant                   0.97
Papalote Taco House                       0.8955
Taco More                                 0.9861
Taquería Chapala                          0.9754
Uncle Julio’s                                  0
Z’Tejas Mexican Restaurant and Grill      0.9894
El Taquito                                0.9583
Santa Catarina Restaurant                      0
Taco Flats                                0.9985
Juan In A Million                         0.9594
Juan In A Million                         0.9942
Pueblo Viejo                                   0
Taco More                                   0.95
Uncle Julio’s                             0.9967
Casa Garcia’s                                  0
Santa Catarina Restaurant                 0.9649
La Condesa                               -0.4852
Tortilleria Rio Grande                         0
Pueblo Viejo                              0.9674
Santa Catarina Restaurant                      0
La Condesa                                0.8779
Casa Maria                                     0
Vazquez Restaurant                        0.8608
Tamale House East                        -0.4588
El Taquito                                0.9642
Santa Catarina Restaurant                      0
Casa Garcia’s                             0.8779
La Fruta Feliz                                 0
La Fruta Feliz                            0.7717

[8022 rows x 1 columns]

In [50]:
sentiment_analysis2['review_text']

restaurant_links
Austin Taco Project                     0.4404
Matt’s El Rancho                             0
Casa Garcia’s                                0
Zocalo Café                             0.9802
Zocalo Café                             0.9985
Manuel’s                                0.6681
Taquería Chapala                        0.9488
Tamale House East                       0.7574
Tortilleria Rio Grande                       0
Uncle Julio’s                           0.9705
Camino Real Restaurant                  0.9108
Pueblo Viejo                                 0
Tortilleria Rio Grande                  0.9715
Tortilleria Rio Grande                  0.9636
Camino Real Restaurant                 -0.6249
Juan In A Million                            0
Los Jaliscienses                       -0.4466
Santa Catarina Restaurant                    0
Taco Flats                              0.9898
Juan In A Million                            0
Tamale House East                      -0.0

In [51]:
sentiment_analysis2 = pd.to_numeric(sentiment_analysis2['review_text'])

In [52]:
sentiment_analysis2 = pd.DataFrame(sentiment_analysis2)

In [53]:
grouped_by_analysis = sentiment_analysis2.groupby(['restaurant_links'])[['review_text']].mean()


In [54]:
grouped_by_analysis

review_text
restaurant_links                                 
Austin Taco Project                      0.378074
Brendas All Natural                      0.479125
Camino Real Restaurant                   0.353783
Casa Garcia’s                            0.372177
Casa Maria                               0.325333
El Taquito                               0.330515
Juan In A Million                        0.382046
La Condesa                               0.309967
La Fruta Feliz                           0.339380
La Morena                                0.405750
Los Jaliscienses                         0.389737
Manuel’s                                 0.367609
Matt’s El Rancho                         0.338704
Papalote Taco House                      0.397693
Pueblo Viejo                             0.387201
Santa Catarina Restaurant                0.400596
Taco Flats                               0.389694
Taco More                                0.375404
Tamale House East                        0.335436
Taquería Chapala                         0.358679
Techo Mezcaleria & Agave Bar             0.459212
Tex-Mex Joe’s                            0.381421
Tortilleria Rio Grande                   0.368242
Uncle Julio’s                            0.310111
Vazquez Restaurant                       0.360565
Zocalo Café                              0.422837
Z’Tejas Mexican Restaurant and Grill     0.324264

In [55]:
grouped_by_analysis = grouped_by_analysis.sort_values(by=['review_text'],ascending = False)

### Recommendation system

In [56]:
grouped_by_restaurant1= grouped_by_restaurant.reset_index()

In [57]:
grouped_by_analysis1 = grouped_by_analysis.reset_index()

In [58]:
grouped_by_analysis1.columns=['restaurant_links','sentiment']

In [59]:
grouped_by_analysis1

restaurant_links  sentiment
0                    Brendas All Natural   0.479125
1           Techo Mezcaleria & Agave Bar   0.459212
2                            Zocalo Café   0.422837
3                              La Morena   0.405750
4              Santa Catarina Restaurant   0.400596
5                    Papalote Taco House   0.397693
6                       Los Jaliscienses   0.389737
7                             Taco Flats   0.389694
8                           Pueblo Viejo   0.387201
9                      Juan In A Million   0.382046
10                         Tex-Mex Joe’s   0.381421
11                   Austin Taco Project   0.378074
12                             Taco More   0.375404
13                         Casa Garcia’s   0.372177
14                Tortilleria Rio Grande   0.368242
15                              Manuel’s   0.367609
16                    Vazquez Restaurant   0.360565
17                      Taquería Chapala   0.358679
18                Camino Real Restaurant   0.353783
19                        La Fruta Feliz   0.339380
20                      Matt’s El Rancho   0.338704
21                     Tamale House East   0.335436
22                            El Taquito   0.330515
23                            Casa Maria   0.325333
24  Z’Tejas Mexican Restaurant and Grill   0.324264
25                         Uncle Julio’s   0.310111
26                            La Condesa   0.309967

In [69]:
def retrieve_recommendations(restaurant_index, num_recommendations=3):
    """
    Retrieves the most similar restaurants for the index of a given restaurant 
    
    Outputs a data frame showing similarity, name, location, category, & rating
    """
    # Formatting the cosine similarity data frame for merging
    similarity = pd.melt(cosine[cosine.index == restaurant_index])
    similarity.columns = (['restIndex', 'cosineSimilarity'])

    # Merging the cosine similarity data frame to the original data frame
    similarity = similarity.merge(
        grouped_by_restaurant1[['restaurant_links','review_text','ratings']],
        left_on=similarity['restIndex'],
        right_index=True)
    similarity = similarity.merge(
    grouped_by_analysis1[['restaurant_links','sentiment']],
    on='restaurant_links', how='inner')
    similarity.drop(['restIndex'], axis=1, inplace=True)
    
    
    

    # Sorting by similarity
    similarity = similarity.sort_values(
        ['cosineSimilarity','sentiment'], ascending=[False,False])[:num_recommendations + 1]
   
    return similarity

In [73]:
retrieve_recommendations(17)

key_0  cosineSimilarity    restaurant_links  \
17     17          1.000000           Taco More   
5       5          0.961944          El Taquito   
24     24          0.955988  Vazquez Restaurant   
19     19          0.953336    Taquería Chapala   

                                          review_text   ratings  sentiment  
17  NoneNoneNoneI went here with my Boyfriend and ...  3.148724   0.375404  
5   Good for really late when most of the other tr...  2.862613   0.330515  
24  NoneNoneVery good Mexican food, good Serrvicce...  2.956094   0.360565  
19  This place is awesome! If you are looking for ...  2.928354   0.358679

### Recommendation system with Average ratings

In [62]:
grouped_by_restaurant1.sort_values(by=['ratings'],ascending=False)

restaurant_links  \
1                    Brendas All Natural   
9                              La Morena   
20          Techo Mezcaleria & Agave Bar   
13                   Papalote Taco House   
14                          Pueblo Viejo   
17                             Taco More   
15             Santa Catarina Restaurant   
8                         La Fruta Feliz   
22                Tortilleria Rio Grande   
21                         Tex-Mex Joe’s   
3                          Casa Garcia’s   
6                      Juan In A Million   
16                            Taco Flats   
25                           Zocalo Café   
24                    Vazquez Restaurant   
10                      Los Jaliscienses   
19                      Taquería Chapala   
0                    Austin Taco Project   
4                             Casa Maria   
2                 Camino Real Restaurant   
5                             El Taquito   
18                     Tamale House East   
11                              Manuel’s   
12                      Matt’s El Rancho   
26  Z’Tejas Mexican Restaurant and Grill   
23                         Uncle Julio’s   
7                             La Condesa   

                                          review_text   ratings  
1   Amazing breakfast tacos!! Lady was super frien...  3.476502  
9   Went in for quick treat knowing they had ice c...  3.476502  
20  NoneFriend: "'Techo' is Spanish for roof."\n\n...  3.251502  
13  We tried 4 different tacos and they were all o...  3.176502  
14  NoneOrdered the taco plate which came with bea...  3.162613  
17  NoneNoneNoneI went here with my Boyfriend and ...  3.148724  
15  NoneNoneTwo years this place has been here and...  3.112613  
8   NoneNoneNoneMy heart. Good food, sweet service...  3.086258  
22  NoneI really wanted to like this place they ha...  3.073724  
21  It was hard to have high expectations,as the r...  3.054021  
3   NoneNoneWhen I'm in town I have to hit this pl...  3.029280  
6   NoneNoneGreat breakfast at great prices. Very ...  2.993169  
16  Love love love love love!! Amazing food amazin...  2.965391  
25  I don't typically care for restaurants that do...  2.957058  
24  NoneNoneVery good Mexican food, good Serrvicce...  2.956094  
10  Food quality and atmosphere are not the issue ...  2.940212  
19  This place is awesome! If you are looking for ...  2.928354  
0   I went here with my boyfriend one evening. It ...  2.909835  
4   I love this place, their breakfast tacos are a...  2.882058  
2   I don't live close to this place, but when I'm...  2.877737  
5   Good for really late when most of the other tr...  2.862613  
18  Finally I found a decent place that has good t...  2.837613  
11  Warning- ripoff scam in progress! I had my din...  2.807058  
12  NoneI was pleasantly surprised by this place. ...  2.793169  
26  NoneNoneGrateful for the complimentary valet a...  2.668169  
23  The fajitas were the bomb.  Marquis made an aw...  2.654280  
7   Great service but portions very small for the ...  2.532058

In [63]:
# Filtering to those from my list with the highest ratings
topRated = grouped_by_restaurant1[grouped_by_restaurant1['ratings'] >= 3]

# Preparing for display
recommendations = topRated[['restaurant_links','review_text','ratings']].sort_values('ratings', ascending=False)

In [71]:
def retrieve_recommendations1(restaurant_index, num_recommendations=27):
    """
    Retrieves the most similar restaurants for the index of a given restaurant 
    
    Outputs a data frame showing similarity, name, location, category, & rating
    """
    # Formatting the cosine similarity data frame for merging
    similarity = pd.melt(cosine[cosine.index == restaurant_index])
    similarity.columns = (['restIndex', 'cosineSimilarity'])

    # Merging the cosine similarity data frame to the original data frame
    similarity = similarity.merge(
        grouped_by_restaurant1[['restaurant_links','review_text','ratings']],
        left_on=similarity['restIndex'],
        right_index=True)
    similarity = similarity.merge(
    grouped_by_analysis1[['restaurant_links','sentiment']],
    on='restaurant_links', how='inner')
    similarity.drop(['restIndex'], axis=1, inplace=True)
    
    
    

    # Sorting by similarity
    similarity = similarity.sort_values(
        ['cosineSimilarity','sentiment'], ascending=[False,False])[:num_recommendations + 1]
   
    return similarity

From the below table, we can see that the restaurants with best ratings have low cosine similarity with the restaurant that customer entered. In conclusion, the simply rating recommendation system cannot fulfill the requirement of the customer. 

In [74]:
retrieve_recommendations1(17)

key_0  cosineSimilarity                      restaurant_links  \
17     17          1.000000                             Taco More   
5       5          0.961944                            El Taquito   
24     24          0.955988                    Vazquez Restaurant   
19     19          0.953336                      Taquería Chapala   
8       8          0.950812                        La Fruta Feliz   
13     13          0.947921                   Papalote Taco House   
2       2          0.947913                Camino Real Restaurant   
10     10          0.946587                      Los Jaliscienses   
21     21          0.945825                         Tex-Mex Joe’s   
16     16          0.945482                            Taco Flats   
22     22          0.944964                Tortilleria Rio Grande   
14     14          0.942893                          Pueblo Viejo   
3       3          0.941288                         Casa Garcia’s   
4       4          0.936775                            Casa Maria   
0       0          0.933802                   Austin Taco Project   
18     18          0.929283                     Tamale House East   
7       7          0.927740                            La Condesa   
11     11          0.925791                              Manuel’s   
15     15          0.925050             Santa Catarina Restaurant   
23     23          0.924036                         Uncle Julio’s   
25     25          0.923879                           Zocalo Café   
6       6          0.913690                     Juan In A Million   
26     26          0.912881  Z’Tejas Mexican Restaurant and Grill   
12     12          0.912676                      Matt’s El Rancho   
20     20          0.762891          Techo Mezcaleria & Agave Bar   
1       1          0.541377                   Brendas All Natural   
9       9          0.355540                             La Morena   

                                          review_text   ratings  sentiment  
17  NoneNoneNoneI went here with my Boyfriend and ...  3.148724   0.375404  
5   Good for really late when most of the other tr...  2.862613   0.330515  
24  NoneNoneVery good Mexican food, good Serrvicce...  2.956094   0.360565  
19  This place is awesome! If you are looking for ...  2.928354   0.358679  
8   NoneNoneNoneMy heart. Good food, sweet service...  3.086258   0.339380  
13  We tried 4 different tacos and they were all o...  3.176502   0.397693  
2   I don't live close to this place, but when I'm...  2.877737   0.353783  
10  Food quality and atmosphere are not the issue ...  2.940212   0.389737  
21  It was hard to have high expectations,as the r...  3.054021   0.381421  
16  Love love love love love!! Amazing food amazin...  2.965391   0.389694  
22  NoneI really wanted to like this place they ha...  3.073724   0.368242  
14  NoneOrdered the taco plate which came with bea...  3.162613   0.387201  
3   NoneNoneWhen I'm in town I have to hit this pl...  3.029280   0.372177  
4   I love this place, their breakfast tacos are a...  2.882058   0.325333  
0   I went here with my boyfriend one evening. It ...  2.909835   0.378074  
18  Finally I found a decent place that has good t...  2.837613   0.335436  
7   Great service but portions very small for the ...  2.532058   0.309967  
11  Warning- ripoff scam in progress! I had my din...  2.807058   0.367609  
15  NoneNoneTwo years this place has been here and...  3.112613   0.400596  
23  The fajitas were the bomb.  Marquis made an aw...  2.654280   0.310111  
25  I don't typically care for restaurants that do...  2.957058   0.422837  
6   NoneNoneGreat breakfast at great prices. Very ...  2.993169   0.382046  
26  NoneNoneGrateful for the complimentary valet a...  2.668169   0.324264  
12  NoneI was pleasantly surprised by this place. ...  2.793169   0.338704  
20  NoneFriend: "'Techo' is Spanish for roof."\n\n...  3.251502   0.459212  
1   Amazing breakfast tacos!! Lady was super frien...  3.476502   0.4